In [1]:
!git clone https://github.com/IsraelAbebe/An-Amharic-News-Text-classification-Dataset

Cloning into 'An-Amharic-News-Text-classification-Dataset'...
remote: Enumerating objects: 30, done.
remote: Counting objects: 100% (30/30), done.
remote: Compressing objects: 100% (29/29), done.
remote: Total 30 (delta 13), reused 4 (delta 1), pack-reused 0
Receiving objects: 100% (30/30), 46.11 MiB | 5.33 MiB/s, done.
Resolving deltas: 100% (13/13), done.


In [12]:
from zipfile import ZipFile
import logging
import boto3
from botocore.exceptions import ClientError
import os
import pandas as pd
from kafka import KafkaProducer
from kafka.errors import KafkaError
from kafka import KafkaConsumer

## Extract data

In [11]:
with ZipFile('An-Amharic-News-Text-classification-Dataset/data/Amharic News Dataset.zip', 'r') as zipObj:
       # Extract all the contents of zip file in different directory
       zipObj.extractall('transcript_data')

## Loading data into bucket function

In [13]:
def upload_file(file_name: str, bucket: str, object_name=None):
    """Upload a file to an S3 bucket
    :param file_name: File to upload
    :param bucket: Bucket to upload to
    :param object_name: S3 object name. If not specified then file_name is used
    :return: True if file was uploaded, else False
    """

    # If S3 object_name was not specified, use file_name
    if object_name is None:
        object_name = os.path.basename(file_name)

    # Upload the file
    s3_client = boto3.client('s3')
    try:
        response = s3_client.upload_file(file_name, bucket, object_name)
    except ClientError as e:
        logging.error(e)
        return False
    return True

## Reading data from bucket function

In [14]:
def load_data_s3(bucket_name='10academy-group2-bucket',file_name='Clean_Amharic.txt'):
    """ Load transcription data from s3 bucket"""
    s3 = boto3.resource(
        service_name='s3',
        region_name='us-east-1'
    )
    # Load file directly into python
    obj = s3.Bucket(bucket_name).Object(file_name).get()
    df = pd.read_csv(obj['Body'])
    return df

## Producers function

In [15]:
def on_send_success(record_metadata):
    print(record_metadata.topic)
    print(record_metadata.partition)
    print(record_metadata.offset)

def on_send_error(excp):
    log.error('I am an errback', exc_info=excp)
    # handle exception
    
def createProducer():
    producer = KafkaProducer(bootstrap_servers=['b-1.demo-cluster-1.9q7lp7.c1.kafka.eu-west-1.amazonaws.com:9092'])
    return producer

def sendMessage(topic, message,producer):
    producer.send(topic, message).add_callback(on_send_success).add_errback(on_send_error)

## Consumer function

In [16]:
def createConsumer(topic):
    consumer = KafkaConsumer(topic,
                             client_id='tests_id',
                             bootstrap_servers=['b-1.demo-cluster-1.9q7lp7.c1.kafka.eu-west-1.amazonaws.com:9092'],
                             auto_offset_reset='earliest',
                             enable_auto_commit=False)
    return consumer

In [17]:
client_id='tests_id'

topic = 'Benkart_Text_Topic'

file_name = 'transcript_data/Amharic News Dataset.csv'

bucket = 'benkart-bucket'

## Upload extracted file into bucket

In [18]:
upload_file(file_name=file_name, bucket=bucket, object_name=None)

True

In [21]:
df = load_data_s3(bucket_name=bucket,file_name='Amharic News Dataset.csv')

In [22]:
df.head()

headline category               date  \
0  የኦሊምፒክ ማጣሪያ ተሳታፊዎች የሚለዩበት ቻምፒዮና እየተካሄደ ይገኛል     ስፖርት   January 14, 2021   
1                                   አዲስ ዘመን ድሮ     መዝናኛ  December 28, 2020   
2             የአረንጓዴ ጎርፍ በጎ አድራጎት አምባሳደሮች ተሰየሙ     ስፖርት    January 6, 2021   
3        የሊጉ በቢዝነስ ሞዴል መመራት አበረታች ጅምር መሆኑ ተገለጸ     ስፖርት    January 6, 2021   
4    የኦሊምፒክ ሥራ አስፈፃሚው እስከ ቶኪዮ ኦሊምፒክ ማግስት ይቀጥላል     ስፖርት    January 6, 2021   

  views                                            article  \
0     2  ብርሃን ፈይሳየኢትዮጵያ ቦክስ ፌዴሬሽን በየዓመቱ የሚያዘጋጀው የክለቦች ቻ...   
1     4   የአዲስ ዘመን ጋዜጣ ቀደምት ዘገባዎች በእጅጉ ተነባቢ ዛሬም ላገኛቸው በ...   
2     6  ቦጋለ አበበየአዲስ አበባ ከተማ አስተዳደር ስፖርት ኮሚሽን ከኢትዮጵያ አረ...   
3     5  ብርሃን ፈይሳአዲስ አበባ፡- የኢትዮጵያ ፕሪምየር ሊግ በሼር ካምፓኒ እንዲ...   
4    12  ቦጋለ አበበ የኢትዮጵያ ኦሊምፒክ ኮሚቴ አርባ አምስተኛ መደበኛ ጠቅላላ ጉ...   

                                link  
0  https://www.press.et/Ama/?p=39481  
1  https://www.press.et/Ama/?p=38334  
2  https://www.press.et/Ama/?p=39010  
3  https://www.press.et/Ama/?p=39011  
4  https://www.press.et/Ama/?p=39012

## Producers

In [26]:
prod = createProducer()

## Create mesages

In [31]:
# create and push msgs to kafka topic through producers
for row in df['article']:
    sendMessage(topic=topic, message=bytes(row, 'utf-8'), producer=prod)

Benkart_Text_Topic
0
0
Benkart_Text_Topic
0
1
Benkart_Text_Topic
0
2
Benkart_Text_Topic
0
3
Benkart_Text_Topic
0
4
Benkart_Text_Topic
0
5
Benkart_Text_Topic
0
6
Benkart_Text_Topic
0
7
Benkart_Text_Topic
0
8
Benkart_Text_Topic
0
9
Benkart_Text_Topic
0
10
Benkart_Text_Topic
0
11
Benkart_Text_Topic
0
12
Benkart_Text_Topic
0
13
Benkart_Text_Topic
0
14
Benkart_Text_Topic
0
15
Benkart_Text_Topic
0
16
Benkart_Text_Topic
0
17
Benkart_Text_Topic
0
18
Benkart_Text_Topic
0
19
Benkart_Text_Topic
0
20
Benkart_Text_Topic
0
21
Benkart_Text_Topic
0
22
Benkart_Text_Topic
0
23
Benkart_Text_Topic
0
24
Benkart_Text_Topic
0
25
Benkart_Text_Topic
0
26
Benkart_Text_Topic
0
27
Benkart_Text_Topic
0
28
Benkart_Text_Topic
0
29
Benkart_Text_Topic
0
30
Benkart_Text_Topic
0
31
Benkart_Text_Topic
0
32
Benkart_Text_Topic
0
33
Benkart_Text_Topic
0
34
Benkart_Text_Topic
0
35
Benkart_Text_Topic
0
36
Benkart_Text_Topic
0
37
Benkart_Text_Topic
0
38
Benkart_Text_Topic
0
39
Benkart_Text_Topic
0
40
Benkart_Text_Topic
0
41
Be

## Stream mesages from Kafka with consumer

In [34]:
consumer = createConsumer(topic=topic)

In [ ]:
for message in consumer:
    # message value and key are raw bytes -- decode if necessary!
    # e.g., for unicode: `message.value.decode('utf-8')`
    print ("%s:%d:%d: value=%s" % (message.topic, message.partition,
                                          message.offset,message.value.decode('utf-8')))

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Benkart_Text_Topic:0:50929: value=ኢትዮጵያ የምግብ እና ስርዐተ ምግብ ዋስትናን ማረጋገጥ ቅድሚያ ከሚሰጣቸው የልማት ተግባራት አንዱ በማድረግ ትኩረት ተሰጥቶ እየተሰራበት መሆኑን ፕሬዝዳንት ሣህለወርቅ ዘውዴ ገለጹ፡፡በኢትዮጵያ በህጻናት ላይ የሚታየውን የመቀንጨር ችግር ለመፍታት የተቀረጸው የሰቆጣ የውሳኔ ሃሳብ ላይ የሚመክረው ጉባኤ በኒውዮርክ ተካሂዷል፡፡በዚህ መድረክ ላይ ንግግር ያደረጉት ፕሬዝዳንት ሣህለወርቅ ዘውዴ እንዳሉት ኢትዮጵያ ባለፉት 16 አመታት የህጻናት መቀንጨርን በ20 በመቶ መቀነስ ችላለች፡፡ከአንድ አመት በፊት የጸደቀው የምግብና የስርዐተ ምግብ ፖሊሲ መቀንጨርን ለመከላከል የተቀረጸውን የሰቆጣን የውሳኔ ሀሳብ ተግባራዊ ለማድረግ ቁልፍ እርምጃ ነው ብለዋል፡፡ችግሩን ለመቅረፍም ከሁሉም አጋሮች ጋር ተባብሮ ለመስራት ኢትዮጵያ ያላትን ቁርጠኝነት የገለጹት ፕሬዝደንት ሣህለወርቅ፣ አጋር አካላትም ድጋፋቸውን የበለጠ አጠናክረው እንዲቀጥሉ ጥሪ አቅርበዋል፡፡በስብሰባው ላይ የተሳተፉት አጋሮች በበኩላቸው፣ እስካሁን የተገኘው ውጤት አበረታች መሆኑን ነው ያመለከቱት፡፡ በቀጣይም በሰቆጣ የውሳኔ ሀሳብ ላይ የተቀመጡት ግቦች እንዲሳኩ ከኢትዮጵያ መንግስት ጋር በቅርበት እንደሚሰሩ አረጋግጠዋል፡፡ጥናቶች እንደሚጠቁሙት በኢትዮጵያ 38 በመቶ የሚሆኑት ህጻናት የመቀንጨር ችግር እንደሚያጋጥማቸው ከፕሬዝዳንት ጽህፈት ቤት ያገኘነው መረጃ ያመለክታል፡፡
Benkart_Text_Topic:0:50930: value=የኢትዮጵያ ኦርቶዶክስ ተዋሕዶ ቤተ ክርስቲያን ብፁዕ ወቅዱስ አቡነ ማቲያስ ቀዳማዊ ፓትሪያርክ ርዕሰ ሊቃነ ጳጳሳት ዘኢትዮጵያ ሊቀጳጳስ ዘአክሱም ወዕጨጌ ዘመንበረ ተክለሃይማኖት በደመራ በዓል ላይ መልዕክት አስተላልፈዋል፡፡‹‹የጎደለውን ፍቅር እና ሠላም፣ 